In [16]:
from gurobipy import*

In [17]:
import json
import copy
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
import shutil


def process_file(file_path):
    
    with open(file_path, 'r') as file:
        data = json.load(file)
        load_actions = data['route']

    # Extract vehicle keys in sorted order
    sorted_vehicle_keys = sorted(data['vehicles'].keys(), key=lambda x: int(x[1:]))

    # Extract the dimensions in sorted order
    vehicle_capacity = np.array([data['vehicles'][vehicle]['dimension'] for vehicle in sorted_vehicle_keys])

    deck_capacity = np.array([data['transporter']['decks'][deck]['capacity'] for deck in sorted(data['transporter']['decks'].keys())])


    # Get the number of stops
    num_stops = len(data['route'])

    # Extract labels from 'decks' keys
    labels = ['Deck ' + str(i + 1) for i in range(len(data['transporter']['decks']))]

    # Number of vehicles
    num_vehicles = len(data['vehicles'])



    # Generate the vehicle_indices dictionary
    vehicle_indices = {vehicle: idx for idx, vehicle in enumerate(data['vehicles'].keys())}


    # Find the maximum deck capacity
    max_deck_capacity = max(deck_capacity)


    # Extract the total capacity
    total_capacity = data['transporter']['total_capacity']


    # Create the deck_via dictionary
    deck_via = {}
    for deck_key, deck_info in data['transporter']['decks'].items():
        # Convert deck key from 'd1' to 1
        deck_number = int(deck_key[1:])
        # Extract accessible decks and convert them from [['d2', 'd4'], ['d3', 'd4']] to [[2, 4], [3, 4]]
        accessible_decks = [[int(d[1:]) for d in sublist] for sublist in deck_info.get('access_via', [])]
        # Assign to deck_via dictionary
        deck_via[deck_number] = accessible_decks

    # Convert dictionary values to NumPy arrays
    deck_via_np = {k: np.array(v) for k, v in deck_via.items()}

    # Initialize the vehicle stops list
    vehicle_stops = []
    
    # Initialize the set of currently loaded vehicles
    current_vehicles = set()

    # Iterate over the load actions to fill vehicle_stops
    for action in load_actions:
        # Unload vehicles if there are any
        if 'unload' in action:
            for vehicle in action['unload']:
                current_vehicles.discard(vehicle_indices[vehicle])
        # Load vehicles if there are any
        if 'load' in action:
            for vehicle in action['load']:
                current_vehicles.add(vehicle_indices[vehicle])

        # Append a sorted list of currently loaded vehicle indices to vehicle_stops
        vehicle_stops.append(sorted(current_vehicles))

    model = Model("feasibility checking")

    x = {}
    for i in range(len(vehicle_capacity)):
        for j in range(len(deck_capacity)):
            x[i,j] = model.addVar(vtype = 'B')

    for k in range(len(vehicle_stops)):
        for j in range(len(deck_capacity)):
            model.addConstr(quicksum(vehicle_capacity[i]*x[i,j]for i in vehicle_stops[k]) <= deck_capacity[j])

    for i in range(len(vehicle_capacity)):
        model.addConstr(quicksum(x[i,j] for j in range(len(deck_capacity))) == 1)


    model.setObjective(quicksum(x[i,j] for i in range(len(vehicle_stops[k])) for j in range(len(deck_capacity))), GRB.MAXIMIZE)
    
    model.setParam('OutputFlag', 0)  # Suppress solver output
    model.optimize()

    # Check the optimization status
    if model.Status == GRB.INFEASIBLE:
        return [file_path, 'NA']
    else:
        filename = os.path.basename(file_path)
        #shutil.move(os.path.join(source_dir, filename), os.path.join(target_dir_s1, filename))
        # If model is feasible, return the objective value or any other result you need
        return [file_path, model.objVal]


In [18]:
# # Define the source directory
# source_dir = r'C:\Users\USER\桌面\soft_infeasible'

# # Define the target directories
# target_dir_s1 = os.path.join(source_dir, 'soft')



# Define the source directory
source_dir = r'/Users/ttonny0326/GitHub_Project/neural-network-and-deep-learning-for-combinatorial-optimisation/data/1M_instances/infeasible'

# Define the target directory
target_dir_s1 = r'/Users/ttonny0326/GitHub_Project/neural-network-and-deep-learning-for-combinatorial-optimisation/data/1M_instances/soft'


# Collect all JSON files in the source directory
input_files = glob.glob(os.path.join(source_dir, '*.json'))

# Filter out files containing 'solution' in the filename
inputFile = [file_path for file_path in input_files if 'solution' not in file_path]


# Results list = soft infeasible instances
results = []

# Process the files and copy if condition is met
for file_path in inputFile:
    result = process_file(file_path)
    if result[1] != 'NA':
        filename = os.path.basename(file_path)
        results.append(filename)
        target_file_path = os.path.join(target_dir_s1, filename)
        shutil.copy(file_path, target_file_path)
        print(f"Copied {filename} to {target_dir_s1}")

print("File copying process completed.")
    


Copied 11CT_147840_s8_v27.json to /Users/ttonny0326/GitHub_Project/neural-network-and-deep-learning-for-combinatorial-optimisation/data/1M_instances/soft
Copied 7CT_181363_s5_v8.json to /Users/ttonny0326/GitHub_Project/neural-network-and-deep-learning-for-combinatorial-optimisation/data/1M_instances/soft
Copied 11CT_97331_s5_v11.json to /Users/ttonny0326/GitHub_Project/neural-network-and-deep-learning-for-combinatorial-optimisation/data/1M_instances/soft
Copied 11CT_417089_s15_v42.json to /Users/ttonny0326/GitHub_Project/neural-network-and-deep-learning-for-combinatorial-optimisation/data/1M_instances/soft
Copied 11CT_386916_s5_v10.json to /Users/ttonny0326/GitHub_Project/neural-network-and-deep-learning-for-combinatorial-optimisation/data/1M_instances/soft
Copied 7CT_423001_s7_v14.json to /Users/ttonny0326/GitHub_Project/neural-network-and-deep-learning-for-combinatorial-optimisation/data/1M_instances/soft
Copied 11CT_372476_s7_v14.json to /Users/ttonny0326/GitHub_Project/neural-netwo

In [19]:
len(results)

44717

In [20]:
len(inputFile)

974065

In [ ]:
# Create a DataFrame from the results, result is soft infeasible 
df = pd.DataFrame(results)

# Save the DataFrame to an Excel file

output_excel_file = r'/Users/ttonny0326/GitHub_Project/neural-network-and-deep-learning-for-combinatorial-optimisation/data/1M_instances/infeasible/soft.xlsx'

# df.to_excel(output_excel_file, index=False)

In [ ]:
df

In [ ]:
df.to_excel(output_excel_file, index=False)